In [1]:
import numpy as np
import matplotlib.pyplot as plt
import h5py
from tensorflow.keras.utils import to_categorical
from sklearn.preprocessing import LabelEncoder
from tensorflow import keras
from tensorflow.keras import layers

In [2]:
from tensorflow.keras.models import load_model
model = load_model('../model_saved/b_tag_model.h5')

2023-05-18 18:57:03.942782: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcuda.so.1'; dlerror: libcuda.so.1: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: /cvmfs/sft.cern.ch/lcg/releases/MCGenerators/thepeg/2.2.3-88592/x86_64-centos7-gcc8-opt/lib/ThePEG:/cvmfs/sft.cern.ch/lcg/releases/MCGenerators/herwig++/7.2.3-35f7a/x86_64-centos7-gcc8-opt/lib/Herwig:/cvmfs/sft.cern.ch/lcg/views/LCG_102cuda/x86_64-centos7-gcc8-opt/lib/python3.9/site-packages/jaxlib/mlir/_mlir_libs:/cvmfs/sft.cern.ch/lcg/views/LCG_102cuda/x86_64-centos7-gcc8-opt/lib/python3.9/site-packages/torch/lib:/cvmfs/sft.cern.ch/lcg/views/LCG_102cuda/x86_64-centos7-gcc8-opt/lib/python3.9/site-packages/onnxruntime/capi/:/cvmfs/sft.cern.ch/lcg/views/LCG_102cuda/x86_64-centos7-gcc8-opt/lib/python3.9/site-packages/tensorflow:/cvmfs/sft.cern.ch/lcg/views/LCG_102cuda/x86_64-centos7-gcc8-opt/lib/python3.9/site-packages/tensorflow/contrib/tensor_forest:/c

In [3]:
import hls4ml
import os
os.environ['PATH'] = '/opt/Xilinx/Vivado/2020.1/bin:' + os.environ['PATH']

In [4]:
int_bit = 10
i = 10
reuse = 2
precision = 'ap_fixed<{},{}>'.format((int_bit+i), int_bit)
fix_int_precision = 'ap_fixed<{},{}>'.format((16+i), 14)
dirc = 'runs/B_tagging_run/r2_{}int_{}frac'.format(int_bit, i)
#First, the baseline model
hls_config = hls4ml.utils.config_from_keras_model(model, granularity='name')

# Set the precision and reuse factor for the full model
hls_config['Model']['Precision'] = precision
hls_config['Model']['ReuseFactor'] = reuse
hls_config['Model']['Strategy'] = 'Resource'

for Layer in hls_config['LayerName'].keys():
    hls_config['LayerName'][Layer]['Precision'] = precision
    hls_config['LayerName'][Layer]['Strategy'] = 'Resource'
    hls_config['LayerName'][Layer]['ReuseFactor'] = reuse
    hls_config['LayerName'][Layer]['weight'] = precision
    hls_config['LayerName'][Layer]['scale'] = precision
    hls_config['LayerName'][Layer]['bias'] = precision
    hls_config['LayerName'][Layer]['accum_t'] = fix_int_precision
    if 'multi_head_attention' in Layer:
        hls_config['LayerName'][Layer]['table_t'] = fix_int_precision
        hls_config['LayerName'][Layer]['inv_range'] = 256
        hls_config['LayerName'][Layer]['exp_range'] = 4
        hls_config['LayerName'][Layer]['table_size'] = 1024
    if 'dense' in Layer:
        hls_config['LayerName'][Layer]['table_t'] = fix_int_precision
        hls_config['LayerName'][Layer]['inv_range'] = 256
        hls_config['LayerName'][Layer]['table_size'] = 1024
        hls_config['LayerName'][Layer]['exp_range'] = 4

cfg = hls4ml.converters.create_config(backend='Vivado')
cfg['IOType']     = 'io_parallel' # Must set this if using CNNs!
cfg['HLSConfig']  = hls_config
cfg['KerasModel'] = model
cfg['OutputDir']  = dirc
cfg['Part'] = 'xcvu13p-fhga2104-2L-e'

hls_model = hls4ml.converters.keras_to_hls(cfg)
# hls_model.compile()
hls_model.build(csim=False, synth=False, vsynth=True)

Interpreting Model
Topology:
Layer name: input_2, layer type: Input
Layer name: multi_head_attention_2, layer type: MultiHeadAttention
Layer name: add_4, layer type: Add
Layer name: dense_8, layer type: Dense
  -> Activation (relu), layer name: dense_8
Layer name: dense_9, layer type: Dense
  -> Activation (linear), layer name: dense_9
Layer name: add_5, layer type: Add
Layer name: multi_head_attention_3, layer type: MultiHeadAttention
Layer name: add_6, layer type: Add
Layer name: dense_10, layer type: Dense
  -> Activation (relu), layer name: dense_10
Layer name: dense_11, layer type: Dense
  -> Activation (linear), layer name: dense_11
Layer name: add_7, layer type: Add
Layer name: multi_head_attention_4, layer type: MultiHeadAttention
Layer name: add_8, layer type: Add
Layer name: dense_12, layer type: Dense
  -> Activation (relu), layer name: dense_12
Layer name: dense_13, layer type: Dense
  -> Activation (linear), layer name: dense_13
Layer name: add_9, layer type: Add
Layer nam

INFO: [HLS 200-10] Setting target device to 'xcvu13p-fhga2104-2L-e'
INFO: [XFORM 203-101] Allowed max sub elements number after partition is 4096.
INFO: [XFORM 203-1161] The maximum of name length is set into 60.
INFO: [XFORM 203-101] Allowed max sub elements number after partition is 4096.
INFO: [XFORM 203-1161] The maximum of name length is set into 60.
***** VIVADO SYNTHESIS *****

****** Vivado v2020.1 (64-bit)
  **** SW Build 2902540 on Wed May 27 19:54:35 MDT 2020
  **** IP Build 2902112 on Wed May 27 22:43:36 MDT 2020
    ** Copyright 1986-2020 Xilinx, Inc. All Rights Reserved.

source vivado_synth.tcl
# set tcldir [file dirname [info script]]
# source [file join $tcldir project.tcl]
## variable project_name
## set project_name "myproject"
## variable backend
## set backend "vivado"
## variable part
## set part "xcvu13p-fhga2104-2L-e"
## variable clock_period
## set clock_period 5
# add_files ${project_name}_prj/solution1/syn/verilog
# synth_design -top ${project_name} -part $pa

INFO: [Synth 8-6157] synthesizing module 'myproject_mux_3849_20_1_1' [/data/hlssynt-users/zhjiang/runs/B_tagging_run/r2_10int_10frac/myproject_prj/solution1/syn/verilog/myproject_mux_3849_20_1_1.v:8]
	Parameter ID bound to: 1 - type: integer 
	Parameter NUM_STAGE bound to: 1 - type: integer 
	Parameter din0_WIDTH bound to: 20 - type: integer 
	Parameter din1_WIDTH bound to: 20 - type: integer 
	Parameter din2_WIDTH bound to: 20 - type: integer 
	Parameter din3_WIDTH bound to: 20 - type: integer 
	Parameter din4_WIDTH bound to: 20 - type: integer 
	Parameter din5_WIDTH bound to: 20 - type: integer 
	Parameter din6_WIDTH bound to: 20 - type: integer 
	Parameter din7_WIDTH bound to: 20 - type: integer 
	Parameter din8_WIDTH bound to: 20 - type: integer 
	Parameter din9_WIDTH bound to: 20 - type: integer 
	Parameter din10_WIDTH bound to: 20 - type: integer 
	Parameter din11_WIDTH bound to: 20 - type: integer 
	Parameter din12_WIDTH bound to: 20 - type: integer 
	Parameter din13_WIDTH bound

INFO: [Synth 8-6155] done synthesizing module 'myproject_mux_3849_20_1_1' (9#1) [/data/hlssynt-users/zhjiang/runs/B_tagging_run/r2_10int_10frac/myproject_prj/solution1/syn/verilog/myproject_mux_3849_20_1_1.v:8]
INFO: [Synth 8-6157] synthesizing module 'myproject_mux_646_20_1_1' [/data/hlssynt-users/zhjiang/runs/B_tagging_run/r2_10int_10frac/myproject_prj/solution1/syn/verilog/myproject_mux_646_20_1_1.v:8]
	Parameter ID bound to: 1 - type: integer 
	Parameter NUM_STAGE bound to: 1 - type: integer 
	Parameter din0_WIDTH bound to: 20 - type: integer 
	Parameter din1_WIDTH bound to: 20 - type: integer 
	Parameter din2_WIDTH bound to: 20 - type: integer 
	Parameter din3_WIDTH bound to: 20 - type: integer 
	Parameter din4_WIDTH bound to: 20 - type: integer 
	Parameter din5_WIDTH bound to: 20 - type: integer 
	Parameter din6_WIDTH bound to: 20 - type: integer 
	Parameter din7_WIDTH bound to: 20 - type: integer 
	Parameter din8_WIDTH bound to: 20 - type: integer 
	Parameter din9_WIDTH bound to

INFO: [Synth 8-6155] done synthesizing module 'myproject_mux_3849_20_1_1_x' (12#1) [/data/hlssynt-users/zhjiang/runs/B_tagging_run/r2_10int_10frac/myproject_prj/solution1/syn/verilog/myproject_mux_3849_20_1_1_x.v:8]
INFO: [Synth 8-6157] synthesizing module 'myproject_mux_646_20_1_1_x' [/data/hlssynt-users/zhjiang/runs/B_tagging_run/r2_10int_10frac/myproject_prj/solution1/syn/verilog/myproject_mux_646_20_1_1_x.v:8]
	Parameter ID bound to: 1 - type: integer 
	Parameter NUM_STAGE bound to: 1 - type: integer 
	Parameter din0_WIDTH bound to: 20 - type: integer 
	Parameter din1_WIDTH bound to: 20 - type: integer 
	Parameter din2_WIDTH bound to: 20 - type: integer 
	Parameter din3_WIDTH bound to: 20 - type: integer 
	Parameter din4_WIDTH bound to: 20 - type: integer 
	Parameter din5_WIDTH bound to: 20 - type: integer 
	Parameter din6_WIDTH bound to: 20 - type: integer 
	Parameter din7_WIDTH bound to: 20 - type: integer 
	Parameter din8_WIDTH bound to: 20 - type: integer 
	Parameter din9_WIDTH

...

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



latency_0_0_0_0_0_0_0_0_0_0_0_0_0_0_0_0_0_0_0_0_0_0_0_s_fu_1441/mul_ln1118_7975_fu_1117_p2_funnel__13                                                       |       8|
|8741  |        mul_ln1118_8029_fu_1188_p2                                                 |\Loop_2_proc_U0/grp_dense_resource_ap_fixed_ap_fixed_20_10_5_3_0_config6_s_fu_3066/myproject_mul_mul_10ns_19ns_28_1_1_U3271/myproject_mul_mul_10ns_19ns_28_1_1_DSP48_15_U/p_funnel__295                                                                                   |       8|
|8742  |        grp_fu_1124_p2                                                             |\multiheadattention_ap_fixed_ap_fixed_config9_U0/dense_out_ap_fixed_ap_fixed_20_10_5_3_0_config9_U0/grp_dense_latency_0_0_0_0_0_0_0_0_0_0_0_0_0_0_0_0_0_0_0_0_0_0_0_s_fu_1441/mul_ln1118_7975_fu_1117_p2_funnel__64                                                       |       8|
|8743  |        grp_fu_1218_p2                                                             |\mu

Synthesis Optimization Runtime : Time (s): cpu = 01:40:02 ; elapsed = 01:44:55 . Memory (MB): peak = 13838.383 ; gain = 11705.051 ; free physical = 54300 ; free virtual = 83912
Synthesis Optimization Complete : Time (s): cpu = 01:40:02 ; elapsed = 01:44:55 . Memory (MB): peak = 13838.383 ; gain = 11705.051 ; free physical = 54501 ; free virtual = 83917
INFO: [Project 1-571] Translating synthesized netlist
Netlist sorting complete. Time (s): cpu = 00:00:18 ; elapsed = 00:00:18 . Memory (MB): peak = 13838.383 ; gain = 0.000 ; free physical = 53124 ; free virtual = 82560
INFO: [Netlist 29-17] Analyzing 65393 Unisim elements for replacement
INFO: [Netlist 29-28] Unisim Transformation completed in 86 CPU seconds
INFO: [Project 1-570] Preparing netlist for logic optimization
INFO: [Opt 31-138] Pushed 0 inverter(s) to 0 load pin(s).
INFO: [Opt 31-422] The CLOCK_DOMAINS attribute on the BRAM cell multiheadattention_ap_fixed_ap_fixed_config16_U0/matrixmul_transpose_ap_fixed_ap_fixed_config16_66

Netlist sorting complete. Time (s): cpu = 00:00:00.37 ; elapsed = 00:00:00.40 . Memory (MB): peak = 13882.500 ; gain = 0.000 ; free physical = 51031 ; free virtual = 80543
INFO: [Project 1-111] Unisim Transformation Summary:
  A total of 9269 instances were transformed.
  BUFG => BUFGCE: 1 instance 
  DSP48E2 => DSP48E2 (DSP_ALU, DSP_A_B_DATA, DSP_C_DATA, DSP_MULTIPLIER, DSP_M_DATA, DSP_OUTPUT, DSP_PREADD, DSP_PREADD_DATA): 7284 instances
  IBUF => IBUF (IBUFCTRL, INBUF): 1804 instances
  RAM32M16 => RAM32M16 (RAMD32(x14), RAMS32(x2)): 180 instances

INFO: [Common 17-83] Releasing license: Synthesis
816 Infos, 190 Warnings, 0 Critical Warnings and 0 Errors encountered.
synth_design completed successfully
synth_design: Time (s): cpu = 01:49:40 ; elapsed = 01:54:16 . Memory (MB): peak = 13882.500 ; gain = 11762.145 ; free physical = 52672 ; free virtual = 82311
# report_utilization -file vivado_synth.rpt
report_utilization: Time (s): cpu = 00:00:10 ; elapsed = 00:00:10 . Memory (MB): pea

{'CSynthesisReport': {'EstimatedClockPeriod': '6.744',
  'BestLatency': '539',
  'WorstLatency': '539',
  'IntervalMin': '84',
  'IntervalMax': '84',
  'BRAM_18K': '2183',
  'DSP48E': '13336',
  'FF': '637484',
  'LUT': '1416661',
  'URAM': '0',
  'AvailableBRAM_18K': '5376',
  'AvailableDSP48E': '12288',
  'AvailableFF': '3456000',
  'AvailableLUT': '1728000',
  'AvailableURAM': '1280'},
 'VivadoSynthReport': {'LUT': '628050',
  'FF': '687780',
  'BRAM_18K': '312',
  'URAM': '0',
  'DSP48E': '7284'}}